In [1]:
import os
import pandas as pd
import matplotlib.pyplot as plt

from scipy import stats
from utils.print import print_block
from data.dataset import REFLACXWithClinicalDataset
from utils.gradcam import get_df_label_pred_img_input_loss, show_gradCAMpp_result

from tqdm.notebook import tqdm
from utils.plot import relabel_ellipse_df, get_ellipses_patch, get_color_coded_ellipses_for_dicom
from utils.transform import TransformFuncs
from copy import copy
import numpy as np
from sklearn.metrics import accuracy_score, roc_auc_score, confusion_matrix, ConfusionMatrixDisplay
import torch
from model.xami import XAMIMultiCocatModal
from data.data_loader import MIMICDataloader

from utils.gradcam import get_df_label_pred_img_input_loss, show_gradCAMpp_result
from utils.train import get_aus_loss



In [2]:
pd.options.mode.chained_assignment = None

# checking if the GPU is available
use_gpu = torch.cuda.is_available()
device = 'cuda' if use_gpu else 'cpu'
print(f"Will be using {device}")

Will be using cuda


In [3]:
reflacx_dataset = REFLACXWithClinicalDataset(image_size=256)

Positive Loss weight:
[0.768546   0.78635013 0.7937685  0.8338279  0.87388724]
Negative Loss weight:
[0.231454   0.21364985 0.20623146 0.1661721  0.12611276]
Random Loss:
0.21026036153991162


In [4]:
cxr_prefix = "cxr"
cxr_clinical_prefix ="cxr_clinical"

cxr_model_name = 'test_0_8162_epoch300_WithoutClincal_dim32_2022-02-07 21_43_31_353207'
cxr_clinical_model_name = 'test_0_8260__epoch300_WithClincal_dim32_2022-02-08 10_03_56_953198'

In [5]:
# load models

cxr_model = XAMIMultiCocatModal(
    reflacx_dataset,
    device,
    use_clinical=False,
    model_dim=32, # was 64
    embeding_dim=64,
    dropout=.2,  # increase the dropout rate did improve the regularization.
    pretrained=True
)
cxr_model.load_state_dict(torch.load(os.path.join('saved_models', cxr_model_name ), map_location=device))
cxr_model.to(device)
cxr_model.eval()


cxr_clinical_model = XAMIMultiCocatModal(
    reflacx_dataset,
    device,
    use_clinical=True,
    model_dim=32, # was 64
    embeding_dim=64,
    dropout=.2,  # increase the dropout rate did improve the regularization.
    pretrained=True
)
cxr_clinical_model.load_state_dict(torch.load(os.path.join('saved_models', cxr_clinical_model_name), map_location=device))
cxr_clinical_model.to(device)
cxr_clinical_model.eval()


# load loss function
loss_fn = get_aus_loss(reflacx_dataset)

In [6]:
color_code_map = {
    'Enlarged cardiac silhouette': 'yellow',
    'Atelectasis': 'red',
    'Pleural abnormality': 'orange',
    'Consolidation': 'lightgreen',
    'Pulmonary edema': 'dodgerblue',
}

In [7]:
## there are 21 case are annotated by 5 different radiologists.
multi_radiologists_dicom_ids = [id for id, v in reflacx_dataset.df['dicom_id'].value_counts().items() if v >= 5]


In [8]:
XAMI_MIMIC_PATH = "D:\XAMI-MIMIC"
mimic_dataloader = MIMICDataloader(XAMI_MIMIC_PATH)

model_input_image_size = reflacx_dataset.image_size
transform_fun = TransformFuncs(image_size=model_input_image_size)

In [9]:
from matplotlib.lines import Line2D

legend_elements = []

for k, v in  color_code_map.items():
    legend_elements.append(Line2D([0], [0], color=v, lw=4, label=k))

In [12]:
fig, subplots = plt.subplots(
    len(multi_radiologists_dicom_ids), 5, figsize=(80, 400), dpi=80, sharex=True)

fig.legend(handles= legend_elements, loc='upper right', prop={'size': 64})

for plot_y, dicom_id in enumerate(multi_radiologists_dicom_ids):
    idxs = [list(reflacx_dataset.df.index).index(id) for id in reflacx_dataset.df[reflacx_dataset.df['dicom_id'].eq(dicom_id)].index]

    for plot_x, i in enumerate(idxs):
        df, labels_df, pred_df, img, loss, model_input = get_df_label_pred_img_input_loss(
            cxr_model, loss_fn, reflacx_dataset, i, device)

        image_size_x = df.iloc[0]['image_size_x']
        image_size_y = df.iloc[0]['image_size_y']

        image_path = df.iloc[0]['image_path']
        subject_id = df.iloc[0]['subject_id']
        reflacx_id = df.iloc[0]['id']

        ellipse_df = pd.read_csv(df['anomaly_location_ellipses_path'].iloc[0])
        relabeled_ellipse_df = relabel_ellipse_df(ellipse_df)

        subplots[plot_y, plot_x].imshow(transform_fun.display_transform(img))

        color_coded_ellipse = get_color_coded_ellipses_for_dicom(
            reflacx_dataset,
            relabeled_ellipse_df,
            image_size_x,
            image_size_y,
            model_input_image_size,
            color_code_map,
        )

        for e in color_coded_ellipse:
            subplots[plot_y, plot_x].add_patch(copy(e))
